# Reference Images Data Collection

This notebook provide the data collection procedure to download Sentinel-2 Images from Google Earth Engine database. This data will be used as the image reference data for building the deep learning model for Farm Boundary Extraction.

### Dependencies

In [ ]:
!pip install -U geemap
!pip install pyshp
!pip install pycrs
!pip install geopandas
!pip install geedim

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 21.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 50.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.6/98.6 kB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 130.5/130.5 kB 823.2 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 30.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 37.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 60.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.4/55.4 kB 2.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 55.6 MB/s eta 0:00:00
  Created wheel for pyperclip: filename=pyperclip-1.8.2-py3-none-any.whl size=11124 sha256=0621164d3d0b7b96d19bdc649fcfeea1dfd5b74fee63d08ed2df5d

In [ ]:
import ee
import geemap

In [ ]:
from google.colab import drive

drive.mount('/content/gdrive/', force_remount=True)

Mounted at /content/gdrive/


In [ ]:
import os
os.chdir('/content/gdrive/MyDrive/Internship/GEE_datacollection')

### Load Sentinel-2 Images

Function to mask clouds using the Sentinel-2 QA band.

In [ ]:
def maskS2clouds(image):
  qa = image.select('QA60')

  # Bits 10 and 11 are clouds and cirrus, respectively.
  cloudBitMask = 1 << 10;
  cirrusBitMask = 1 << 11;

  # Both flags should be set to zero, indicating clear conditions.
  mask = qa.bitwiseAnd(cloudBitMask).eq(0) and (qa.bitwiseAnd(cirrusBitMask).eq(0));

  return image.updateMask(mask).divide(10000)

Load Sentinel-2 Images

In [ ]:
Map = geemap.Map(center=[1.057, 34.927], zoom=10)

# Load Sentinel-2 images for the early season of maze farming (March-April)
dataset = ee.ImageCollection('COPERNICUS/S2_SR').filterDate('2022-03-01', '2022-04-30').filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE',10)).map(maskS2clouds)
# Select only Blue/B2, Green/B3, Red/B4, and NIR/B8 bands
image = dataset.median().select(['B2', 'B3', 'B4', 'B8'])

# Visualise the images
vis = {'min': 0.0, 'max': 0.3, 'bands': ['B4', 'B3', 'B2']}
Map.addLayer(image, vis, "sentinel2", True)

Map

To authorize access needed by Earth Engine, open the following URL in a web browser and follow the instructions. If the web browser does not start automatically, please manually browse the URL below.

    https://code.earthengine.google.com/client-auth?scopes=https%3A//www.googleapis.com/auth/earthengine%20https%3A//www.googleapis.com/auth/devstorage.full_control&request_id=gBN60xXBKiK42DpPWZ3_m_66hcFx7qyE201RYeQWrLs&tc=CzNRV5Yl_2TC955KBVFxVsgm9pAgauF5y-D0fRZ8eqQ&cc=KY4dQRrCV7M_dMK6H94BHXvIvozWRloqoakOPztzjro

The authorization workflow will generate a code, which you should paste in the box below.
Enter verification code: 4/1AbUR2VMY6Nocg1w0_6voqbeRi0Op40P0g1M3K4gW_p_p1xjrZNuZDjNsLno

Successfully saved authorization token.


Map(center=[1.057, 34.927], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(childr…

### Load Grid

Load grid of the study area, i.e. Trans-Nzoia, Kenya. The grid is set to have size of 256x256 pixels for the training propose.

In [ ]:
in_shp_grid = '/content/gdrive/MyDrive/Internship/GEE_datacollection/area/grid_trans_nzoia_255.shp'
Map.add_shapefile(in_shp_grid, layer_name="Grid")

adm_transnzoia = '/content/gdrive/MyDrive/Internship/GEE_datacollection/area/trans_nzoia.shp'
Map.add_shapefile(adm_transnzoia, layer_name="Study Area")

grid = geemap.shp_to_ee(in_shp_grid)

### Download Images

In [ ]:
# Define the output directory of the Sentinel-2 images
out_dir = os.path.expanduser('/content/gdrive/MyDrive/Internship/GEE_datacollection/Kenya_Trans-Nzoia_Sentinel2')

In [ ]:
geemap.download_ee_image_tiles(
    image, grid, out_dir, prefix="TransNzoia_", crs="EPSG:32637", scale=10
)

TransNzoia_001.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_002.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_003.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_004.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_005.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

...

TransNzoia_731.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_732.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_733.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_734.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)

TransNzoia_735.tif: |          | 0.00/1.05M (raw) [  0.0%] in 00:00 (eta:     ?)